In [1]:
import os
import pandas

In [2]:
path = os.path.join('data', 'problems.tsv')
problem_df = pandas.read_table(path)
problem_df['name_lower'] = list(map(str.lower, problem_df.problem))
problem_df[:3]

problem_definition_id                        problem  indications  \
0                  63467                   Hypertension          242   
1                  63468         Essential Hypertension          204   
2                  63470  Benign Essential Hypertension          190   

                      name_lower  
0                   hypertension  
1         essential hypertension  
2  benign essential hypertension

In [3]:
len(problem_df)

1596

In [4]:
url = 'http://git.dhimmel.com/disease-ontology/data/term-names.tsv'
doterm_df = pandas.read_table(url)
doterm_df['name_lower'] = list(map(str.lower, doterm_df.name))
set(doterm_df.type)

{'exact-synonym', 'name', 'narrow-synonym', 'related-synonym'}

In [5]:
doterm_df = doterm_df.query("type in ['exact-synonym', 'name']")
doterm_df[:3]

doid                                 name           type  \
0  DOID:0050911             appendix carcinoid tumor           name   
1  DOID:0050911  appendix carcinoid endocrine tumour  exact-synonym   
2  DOID:0050703     infancy electroclinical syndrome           name   

                            name_lower  
0             appendix carcinoid tumor  
1  appendix carcinoid endocrine tumour  
2     infancy electroclinical syndrome

In [6]:
domap_df = problem_df.merge(doterm_df, how='left', on='name_lower')
path = os.path.join('data', 'problem-to-doid.tsv')
domap_df.to_csv(path, index=False, sep='\t')

In [7]:
pair_df = domap_df[['problem_definition_id', 'doid']].dropna().drop_duplicates()
len(pair_df)

367

In [8]:
domap_df[:50]

problem_definition_id                                            problem  \
0                   63467                                       Hypertension   
1                   63468                             Essential Hypertension   
2                   63470                      Benign Essential Hypertension   
3                   63470                      Benign Essential Hypertension   
4                   69380                                  Diabetes Mellitus   
5                   69402                Diabetes Mellitus Poorly Controlled   
6                   69381                          Type II Diabetes Mellitus   
7                   76351                                         Depression   
8                   62598                                  Allergic Rhinitis   
9                   74988                                   Seizure Disorder   
10                  62975                            Coronary Artery Disease   
11                  70455                               Rheumatoid Arthritis   
12                  77891                  Acute Upper Respiratory Infection   
13                  76388                               Bipolar Disorder NOS   
14                  60869                                              Cough   
15                  64181                                             Asthma   
16                  75002  Partial Complex Psychomotor Seizure With Intra...   
17                  75125                                 Multiple Sclerosis   
18                  67970                                     Hyperlipidemia   
19                  76357                        Major Depression, Recurrent   
20                  75080                                Parkinson's Disease   
21                  70475                                        Scleroderma   
22                  70475                                        Scleroderma   
23                  63217                           Congestive Heart Failure   
24                  64688                                  Esophageal Reflux   
25                  91089                                    Lower Back Pain   
26                  76272                           Schizoaffective Disorder   
27                  60899                                     Abdominal Pain   
28                  76835                                      HIV Infection   
29                  61118                                  Anxiety (Symptom)   
30                  62588                        Chronic Ethmoidal Sinusitis   
31                  62588                        Chronic Ethmoidal Sinusitis   
32                  69258                                     Hypothyroidism   
33                 278350                                             Eczema   
34                  64118                                   Acute Bronchitis   
35                  74533                                  Migraine Headache   
36                  62916                                Atrial Fibrillation   
37                  76536                       Generalized Anxiety Disorder   
38                 275486                                ADHD, Combined Type   
39                  62578                                    Acute Sinusitis   
40                  65762                            Urinary Tract Infection   
41                  61108                                           Insomnia   
42                 166777                                       Constipation   
43                  76306                            Episodic Mood Disorders   
44                  64205              Chronic Obstructive Pulmonary Disease   
45                  64205              Chronic Obstructive Pulmonary Disease   
46                 251528                                 Acute Otitis Media   
47                 297231                                           Epilepsy   
48                  76307                                   Bipolar Disorder   
49  

In [9]:
mapped_problems = set(pair_df.problem_definition_id)

In [10]:
len(mapped_problems) / len(problem_df)

0.2286967418546366

In [18]:
len(mapped_problems)

365

In [11]:
# Find problems that mapped to multiple DO terms
duplicates = set(pair_df[pair_df.duplicated('problem_definition_id')].problem_definition_id)
domap_df[domap_df.problem_definition_id.isin(duplicates)]

problem_definition_id              problem  indications  \
21                   70475          Scleroderma           63   
22                   70475          Scleroderma           63   
932                 167200  Premature Menopause            2   
933                 167200  Premature Menopause            2   
934                 167200  Premature Menopause            2   

              name_lower        doid                 name           type  
21           scleroderma    DOID:419          scleroderma           name  
22           scleroderma    DOID:418          Scleroderma  exact-synonym  
932  premature menopause  DOID:10787  premature menopause           name  
933  premature menopause  DOID:10787  Premature menopause  exact-synonym  
934  premature menopause   DOID:5426  premature menopause  exact-synonym

In [16]:
url = 'http://git.dhimmel.com/disease-ontology/data/slim-terms.tsv'
doslim_df = pandas.read_table(url)
len(doslim_df)

137

In [17]:
sum(doslim_df.doid.isin(set(pair_df.doid)))

50

In [24]:
# with propagation
url = 'http://git.dhimmel.com/disease-ontology/data/slim-terms-prop.tsv'
doslim_df = pandas.read_table(url)
len(set(doslim_df.slim_id[doslim_df.subsumed_id.isin(set(pair_df.doid))]))

55